#Preparation


#Install dependency and download data


*   Install ffmpeg for cutting the video
*   Download Timecode.py for timecode encoding purpose (self development)
*   Download example.mp4 (source)
*   Download expected.mp4 (expected output)



In [20]:
!apt install ffmpeg
!wget https://raw.githubusercontent.com/ming0520/Timecode/master/Timecode.py
!wget https://github.com/ming0520/FYP-GITHUB/raw/master/Example%20Video/example.mp4
!wget https://github.com/ming0520/FYP-GITHUB/raw/master/Example%20Video/expected.mp4

Reading package lists... Done
Building dependency tree       
Reading state information... Done
ffmpeg is already the newest version (7:3.4.6-0ubuntu0.18.04.1).
0 upgraded, 0 newly installed, 0 to remove and 32 not upgraded.
--2020-06-09 12:28:01--  https://raw.githubusercontent.com/ming0520/Timecode/master/Timecode.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 151.101.0.133, 151.101.64.133, 151.101.128.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|151.101.0.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 3469 (3.4K) [text/plain]
Saving to: ‘Timecode.py’

Timecode.py         100%[===================>]   3.39K  --.-KB/s    in 0s      

2020-06-09 12:28:02 (54.4 MB/s) - ‘Timecode.py’ saved [3469/3469]

--2020-06-09 12:28:03--  https://github.com/ming0520/FYP-GITHUB/raw/master/Example%20Video/example.mp4
Resolving github.com (github.com)... 140.82.114.3
Connecting to github.com (github.com)|140.82.114.3|:

## Import library

In [0]:
#for display the video in colab
from IPython.display import HTML
from base64 import b64encode
'''auto-editor.py'''
#python auto-editor.py lib.mp4 --frame_margin 8 --silent_threshold 0.03
# external python libraries
from scipy.io import wavfile
import numpy as np

# internal python libraries
import math
import os
import subprocess
from shutil import move, rmtree, copyfile

# developed library
from Timecode import Timecode

#Import class

file = path for file <br>
ba = desired audio bit rate, default 160000 <br>
ac = audio channel (mono 1 or stearo 2), default mono 1<br>
ar = audio rate = sample rate (in Hz), default 44100 <br>
output_format = desired output format for temporary audio file, default .wav <br>
frame_rate = fps of video, default = 30.0 <br>
st = silent threshold =


In [0]:
class AutoEdit:
    def __init__(self, file=None, ba='160000', ac='1', ar='44100',output_format='.wav', frame_rate = 30.0, 
                 st = 0.04, fm = 4, lt = 2.00, verbose = False):
        #parameter for ffmpeg to convert the file
        self.INPUT_FILE = file
        self.FILENAME = file.split('.')[0]
        self.AUDIO_OUTPUT_FORMAT = output_format
        self.AUDIO_OUTPUT = f'{self.FILENAME}{self.AUDIO_OUTPUT_FORMAT}'
        
        self.BITRATE_AUDIO = ba
        self.AUDIO_CHANEL = ac
        self.AUDIO_RATE = ar
        self.FRAME_RATE = frame_rate
        
        self.FRAME_MARGIN = fm
        self.SILENT_THRESHOLD = st
        self.LOUDNESS_THRESHOLD = lt
        
        self.VERBOSE = verbose
        
        self.audioData = None
        self.sampleRate = None
        
        self.audioSampleCount = None
        self.maxAudioVolume = None
        self.samplesPerFrame = None
        self.audioFrameCount = None
        self.hasLoudAudio = None
        
        self.chunks = None
        self.shouldIncludeFrame = None
        self.timecodeList = None
        self.chunks_path = 'chunks.txt'
    
    def extract_audio(self):
        if self.INPUT_FILE == None:
            print("No input file!")
            
        cmd = ['ffmpeg', '-y' ,'-i',self.INPUT_FILE,'-acodec','pcm_s16le' ,'-b:a', self.BITRATE_AUDIO, '-ac', self.AUDIO_CHANEL, 
               '-ar', self.AUDIO_RATE, '-vn', f'{self.AUDIO_OUTPUT}']
        #ffmpeg -i "%%a" -acodec pcm_s16le -ac 1 -ar 16000 -af lowpass=3000,highpass=200 "converted\%%~na.wav
        if(not self.VERBOSE):
            cmd.extend(['-nostats', '-loglevel', '0'])
        subprocess.call(cmd)
        
    def get_max_volume(self,s):
        maxv = float(np.max(s))
        minv = float(np.min(s))
        return max(maxv, -minv)

    def load_audio(self):
        self.sampleRate,self.audioData = wavfile.read(f'{self.AUDIO_OUTPUT}')
        self.audioSampleCount = self.audioData.shape[0]
        self.maxAudioVolume = self.get_max_volume(self.audioData)
        self.samplesPerFrame = self.sampleRate / self.FRAME_RATE
        self.audioFrameCount = int(math.ceil(self.audioSampleCount / self.samplesPerFrame))
    
    def get_shape(self):
        return self.audioData.shape
    
    def calc_has_loud_audio(self):
        self.hasLoudAudio = np.zeros((self.audioFrameCount))
        
        for i in range(self.audioFrameCount):
            start = int(i * self.samplesPerFrame)
            end = min( int( (i+1) * self.samplesPerFrame ), self.audioSampleCount)
            audiochunks = self.audioData[start:end]
            maxchunksVolume = self.get_max_volume(audiochunks) / self.maxAudioVolume
            
            if(maxchunksVolume >= self.LOUDNESS_THRESHOLD):
                self.hasLoudAudio[i] = 2
            elif(maxchunksVolume >= self.SILENT_THRESHOLD):
                self.hasLoudAudio[i] = 1
    
    def calc_should_include_frame(self):
        self.shouldIncludeFrame = np.zeros((self.audioFrameCount))
        self.chunks = [[0,0,0]]
        
        for i in range(self.audioFrameCount):
            start = int(max(0, i-self.FRAME_MARGIN))
            end = int(min(self.audioFrameCount, i+1+self.FRAME_MARGIN))
            self.shouldIncludeFrame[i] = min(1,np.max(self.hasLoudAudio[start:end]))

            if(i >= 1 and self.shouldIncludeFrame[i] != self.shouldIncludeFrame[i-1]):
                self.chunks.append([self.chunks[-1][1], i, self.shouldIncludeFrame[i-1]])
        self.chunks.append([self.chunks[-1][1], self.audioFrameCount, self.shouldIncludeFrame[i-1]])
        self.chunks = self.chunks[1:]
        
    def calc_timecode(self):
        self.timecodeList = []
        
        for chunk in self.chunks:
            startTime = Timecode(fps=self.FRAME_RATE)
            endTime = Timecode(fps=self.FRAME_RATE)
            
            startTime.set_by_frames(chunk[0])
            endTime.set_by_frames(chunk[1])
            isInclude = chunk[2]
            
            self.timecodeList.append([startTime,endTime,isInclude])
    
    def produce_concat_file(self):
        if os.path.exists(self.chunks_path):
            os.remove(self.chunks_path)
            
        with open(self.chunks_path, 'w') as f:
            for index in range(len(self.timecodeList)):
                isInclude = float(self.timecodeList[index][2])
                if isInclude < 1:
                    continue;
                startTime = self.timecodeList[index][0].get_timecode_ffmpeg()
                endTime = self.timecodeList[index][1].get_timecode_ffmpeg()
                f.write(f'file {self.INPUT_FILE}\ninpoint {startTime}\noutpoint {endTime}\n')
    
    def export_video(self):
        concat = ['ffmpeg','-y','-f','concat','-safe','0','-i', f'{self.chunks_path}',
                 '-async','1','-framerate', f'{self.FRAME_RATE}','-b:a', f'{self.BITRATE_AUDIO}',
                 '-c:v', 'copy', '-ar', f'{self.AUDIO_RATE}', '-ac', f'{self.AUDIO_CHANEL}',
                 '-c:a','aac','-movflags','+faststart',f'{self.FILENAME}_EDITED.mp4']
        subprocess.call(concat)
        
    def auto_process(self):
        try:
            self.extract_audio()
            self.load_audio()
            self.calc_has_loud_audio()
            self.calc_should_include_frame()
            self.calc_timecode()
            self.produce_concat_file()
            self.export_video()
            if(self.VERBOSE):
                print(f'Exported {self.FILENAME}_EDITED.mp4 successfully!')
        except:
            print('Return error auto_process')

In [0]:
cut = AutoEdit(file='example.mp4',verbose=True)

In [35]:
cut.extract_audio()
cut.load_audio()
print(f'INPUT={cut.INPUT_FILE} AUDIO={cut.AUDIO_OUTPUT}')
print(f'audioSampleCount={cut.audioSampleCount} maxAudioVolume={cut.maxAudioVolume} samplesPerFrame={cut.samplesPerFrame} audioFrameCount={cut.audioFrameCount}')

INPUT=example.mp4 AUDIO=example.wav
audioSampleCount=1870311 maxAudioVolume=11345.0 samplesPerFrame=1470.0 audioFrameCount=1273


In [0]:
cut.calc_has_loud_audio()
cut.calc_should_include_frame()
cut.calc_timecode()

In [0]:
cut.produce_concat_file()
cut.export_video()

<video controls src="example.mp4" />

In [57]:
mp4 = open('example.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

In [58]:
mp4 = open('expected.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

In [59]:
mp4 = open('example_EDITED.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)